<a href="https://colab.research.google.com/github/qahtanaa/OnSubGroupFairness/blob/main/German_close_smote_total_ratio_NN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%reset -f

In [2]:
!pip install aif360

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 259.7/259.7 kB 4.8 MB/s eta 0:00:00


In [3]:
import numpy as np
import pandas as pd
from aif360.metrics import utils
from scipy.sparse import issparse
from sklearn.preprocessing import LabelEncoder, OrdinalEncoder
from aif360.metrics import BinaryLabelDatasetMetric
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import random
from sklearn.neighbors import NearestNeighbors
from sympy import Symbol
from sympy.solvers import solve

pip install 'aif360[Reductions]'
pip install 'aif360[Reductions]'
pip install 'aif360[inFairness]'
pip install 'aif360[Reductions]'


In [4]:
# remember to import raw_dataset_german
df = pd.read_csv('/content/raw_dataset_german.csv')

In [5]:
#so now I have the German dataframe, I want to change the age and personal_status
def convert_age_to_category(age):
    if age >= 25:
        return 1 #'Adult'
    else:
        return 0 #'Youth'

def convert_sex(sex):
  if sex == 'male':
    return 1 #male
  else:
    return 0 #female

df['age'] = df['age'].apply(convert_age_to_category)
df['personal_status'] = df['personal_status'].apply(convert_sex)

print(df.head())

  status  month credit_history purpose  credit_amount savings employment  \
0    A11      6            A34     A43           1169     A65        A75   
1    A12     48            A32     A43           5951     A61        A73   
2    A14     12            A34     A46           2096     A61        A74   
3    A11     42            A32     A42           7882     A61        A74   
4    A11     24            A33     A40           4870     A61        A73   

   investment_as_income_percentage  personal_status other_debtors  ...  \
0                                4                1          A101  ...   
1                                2                0          A101  ...   
2                                2                1          A101  ...   
3                                2                1          A103  ...   
4                                3                1          A101  ...   

   property age  installment_plans housing number_of_credits  skill_level  \
0      A121   1      



---

---

DATA PREPARATION

In [6]:
class DataPreparation():
  """
  ........
  """
  def __init__(self, df, sensitive, label, priv, unpriv, fav, unfav, categorical = [] ):
      """
      Construct all necessary attributes for the data preparation.

      df : (pandas DataFrame) containing the data
      sensitive : (list(str)) specifying the column names of all sensitive features
      label : (str) specifying the label column
      priv : (list(dicts)) representation of the privileged groups
      unpriv : (list(dicts)) representation of the unprivileged groups
      fav : (str/int/..) value representing the favorable label
      unfav : (str/int/..) value representing the unfavorable label
      categorical : (list(str)) (optional) specifying column names of categorical features
      """
      self.df = df
      self.sensitive = sensitive
      self.label = label
      self.priv = priv
      self.unpriv = unpriv
      self.fav = fav
      self.unfav = unfav
      self.categorical = categorical


  def detect_missing_values(self):
      """
      Detect rows with missing values and remove them from the DataFrame.
      """
      initial_rows = len(self.df)
      self.df = self.df.dropna()
      removed_rows = initial_rows - len(self.df)

      if removed_rows > 0:
          print(f"Detected {removed_rows} rows with missing values. Removed them.")
      else:
          print("No missing values detected.") #pass

  def binary_label(self):
      """
      Check that the decision label is made of two values, change it as a binary representation
      where favorable label = 1, unfavorable label = 0.
      """
      number_label_values = self.df[self.label].nunique()
      if number_label_values == 2:
        print(f"The '{self.label}' column has only two unique values.")
        self.df[self.label].replace([self.unfav, self.fav], [0, 1], inplace=True)
      else:
        print(f"The '{self.label}' column does not have exactly two unique values, as it should.")

  def find_categorical_attributes(self):
      """
      find the categorical attributes
      """
      self.attribute_types = {}

      for column in self.df.columns:
          # Skip the 'Group' column
          if column == 'Group':
              continue
          # if the column has already been classified as categorical by the user, leave it cat
          elif column in self.categorical:
              self.attribute_types[column] = 'Categorical'
              continue
          # if the column has only two distinguished values, consider it categorical
          elif self.df[column].nunique() == 2:
            self.attribute_types[column] = 'Categorical'
            continue
          else: #if it's not the group column, or if it's not been classified as categorical by the user, check every value of the column
            num_float = 0
            num_text = 0
            thresh = 0.99
            num_att_in_column = len(self.df[column])

            for value in self.df[column]:  # Accessing all values in the column
              # Attempt to convert the value to a float
              try:
                float(value)
                num_float += 1
                continue  # Move to the next value
              except ValueError:
                pass  # If it's not a float, continue to the next check
              # If it's not an integer or a float, consider it as text
              num_text += 1

            # now see if it's categorical or numerical
            if num_float / num_att_in_column > thresh:
              self.attribute_types[column] = 'Numerical'
              continue
            else:
              self.attribute_types[column] = 'Categorical'

      #encode the categorical attributes
      # Initialize cat_features list, to have if boolean
      self.cat_features = []
      # Iterate over attribute names and determine whether they are categorical or numerical
      for attr in self.attribute_types:
          self.cat_features.append(self.attribute_types[attr] == 'Categorical')

      encoder_dict = dict()
      #self.df = self.df.drop('Group', axis=1)
      self.columns_categorical = self.df.columns[self.cat_features]

      # for each categorical column, encode it
      for column in self.columns_categorical:
          le = LabelEncoder()
          self.df[column] = le.fit_transform(self.df[column].values)
          mapping = dict(zip(le.classes_, range(len(le.classes_))))
          encoder_dict[column] = mapping
      #print(X)

      # Invert the boolean values in the list using list comprehension
      self.numerical_features = [not feature for feature in self.cat_features]
      # Use the inverted list to select numerical columns
      self.columns_numerical = self.df.columns[self.numerical_features]

      # int columns to float, otherwise gower has problems
      for column in self.columns_numerical:
          self.df[column] = self.df[column].astype(float)

      return self.attribute_types, self.cat_features, self.numerical_features


  def create_group_column(self):
      """
      Create a 'Group' column in the DataFrame based on protected attributes, privileged/unprivileged conditions, and label.
      """
      group_combinations = pd.MultiIndex.from_product([self.df[sensitive].unique() for sensitive in self.sensitive] + [self.df[self.label].unique()], names=self.sensitive + [self.label])
      #print(group_combinations)
      print(list(enumerate(group_combinations)))
      # Create a mapping between group combinations and their corresponding numbers
      group_mapping = {group: idx for idx, group in enumerate(group_combinations)}
      reverse_group_mapping = {idx: group for group, idx in group_mapping.items()}  # Create reverse mapping
      # Apply the mapping to create a new column in the DataFrame
      self.df['Group'] = pd.MultiIndex.from_frame(self.df[self.sensitive + [self.label]]).map(group_mapping)

      return reverse_group_mapping #enumerate(group_combinations)


  def train_test_split(self):
      #stratific based on the group
      X = self.df.loc[:, self.df.columns != self.label]
      y = self.df[self.label]

      self.X_train, self.X_test, self.y_train, self.y_test = train_test_split(X, y, test_size=0.3, shuffle = True, stratify = self.df['Group']) #, random_state=42
      #print(self.X_train, self.y_train, self.X_test, self.y_test)
      #print(type(self.y_train))
      return self.X_train, self.y_train, self.X_test, self.y_test

  def standardization_numerical(self):
      # Select only the numerical columns
      train_dataset_numerical = self.X_train[self.columns_numerical]
      test_dataset_numerical = self.X_test[self.columns_numerical]

      # Create a StandardScaler instance and fit it to the training dataset
      scaler = StandardScaler().fit(train_dataset_numerical)

      # Transform the numerical features in the training and test datasets using the trained scaler
      train_dataset_scaled_numerical = scaler.transform(train_dataset_numerical)
      test_dataset_scaled_numerical = scaler.transform(test_dataset_numerical)

      # Update the training and test datasets with the scaled numerical features
      self.X_train[self.columns_numerical] = train_dataset_scaled_numerical
      self.X_test[self.columns_numerical] = test_dataset_scaled_numerical

      #concatenate X_train with y_train, and X_test with y_test
      self.X_train = pd.concat([self.X_train, self.y_train], axis=1)
      self.X_test = pd.concat([self.X_test, self.y_test], axis=1)
      return self.X_train, self.X_test

  def prepare(self):
      """
      Perform all preprocessing steps.
      """
      self.detect_missing_values()
      self.binary_label()
      self.find_categorical_attributes()
      self.create_group_column()
      self.train_test_split()
      self.standardization_numerical()
      return self

In [7]:
#use the DataPreparation class to preprocess the dataframe
data_prep = DataPreparation(df, ['personal_status','age'], 'credit', [1, 1], [0, 0], 1, 2)
data_prep.prepare()

# use this reset index to have indices from 0 to len(df)
data_prep.df = data_prep.df.reset_index(drop=True)
print(data_prep.df)

No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
     status  month  credit_history  purpose  credit_amount  savings  \
0         0    6.0               4        4         1169.0        4   
1         1   48.0               2        4         5951.0        0   
2         3   12.0               4        7         2096.0        0   
3         0   42.0               2        3         7882.0        0   
4         0   24.0               3        0         4870.0        0   
..      ...    ...             ...      ...            ...      ...   
995       3   12.0               2        3         1736.0        0   
996       0   30.0               2        1         3857.0        0   
997       3   12.0               2        4          804.0        0   
998       0   45.0               2        4         1845.0        0   
999       1   

In [18]:
X_train, X_test = data_prep.X_train, data_prep.X_test
X_train = X_train.reset_index(drop=True)
X_test = X_test.reset_index(drop=True)

In [20]:
# Count instances from each group in X_train
group_counts_train = X_train['Group'].value_counts().sort_index()

# Count instances from each group in X_test
group_counts_test = X_test['Group'].value_counts().sort_index()

print("Group counts in X_train:")
print(group_counts_train)

print("\nGroup counts in X_test:")
print(group_counts_test)

Group counts in X_train:
Group
0    321
1    116
2     28
3     18
4    107
5     51
6     34
7     25
Name: count, dtype: int64

Group counts in X_test:
Group
0    138
1     50
2     12
3      7
4     46
5     22
6     14
7     11
Name: count, dtype: int64


In [22]:
total_ratio = (X_train['credit'] == 1).sum() / (X_train['credit'] == 0).sum()

In [12]:
attribute_types = data_prep.attribute_types
print(attribute_types)

{'status': 'Categorical', 'month': 'Numerical', 'credit_history': 'Categorical', 'purpose': 'Categorical', 'credit_amount': 'Numerical', 'savings': 'Categorical', 'employment': 'Categorical', 'investment_as_income_percentage': 'Numerical', 'personal_status': 'Categorical', 'other_debtors': 'Categorical', 'residence_since': 'Numerical', 'property': 'Categorical', 'age': 'Categorical', 'installment_plans': 'Categorical', 'housing': 'Categorical', 'number_of_credits': 'Numerical', 'skill_level': 'Categorical', 'people_liable_for': 'Categorical', 'telephone': 'Categorical', 'foreign_worker': 'Categorical', 'credit': 'Categorical'}


In [13]:
cat_features = data_prep.cat_features
numerical_features = data_prep.numerical_features
reverse_group_mapping = data_prep.create_group_column()
theoretical_num_groups = len(reverse_group_mapping)

[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]




---


---

DISTANCES \ only Gower, for now

In [ ]:
# !pip install gower
# import gower

In [ ]:
# def gower_distance(df_train, cat_features_boolean, n=5):
#     """
#     ndary: ndarray, that if the dataframe X precedentemente converted to numpy, it has all columns beside the Group one (yes, it also has
#           the label column)
#     cat_features: array of T/F where True = the attribute is categorical, False = the attribute is numerical
#     n = number or closest neighbors
#     """
#     X = df_train
#     cat_features = cat_features_boolean
#     # n+1 because in the matrix with indices, at the first position there's the point itself
#     n = n + 1

#     # compute the matrix of the distances using Gower
#     matrix_dist_gower = gower.gower_matrix(X, cat_features=cat_features)

#     # compute the matrix with top-n neighbors and the distance values
#     num_rows_gower = X.shape[0]

#     # Initialize a list to store the results
#     matrix_neighbors_gower = []

#     # Mapping between original indices and indices between 0 and 699
#     index_mapping = {original_index: i for i, original_index in enumerate(X.index)}
#     print(index_mapping)
#     reverse_index_mapping = {v: k for k, v in index_mapping.items()}
#     print(reverse_index_mapping)

#     # Loop through each row
#     for i in range(num_rows_gower):
#         top_n_neighbors_gower = gower.gower_topn(X.iloc[i:i + 1, :], X.iloc[:, :], cat_features=cat_features, n=n)
#         #mapped_neighbors = [{'index': index_mapping[item['index']], 'values': item['values']} for item in top_n_neighbors_gower]
#         #print(top_n_neighbors_gower)
#         matrix_neighbors_gower.append(top_n_neighbors_gower)

#     # Convert the list of dictionaries to a matrix
#     matrix_neighbors_gower_index = np.array([item['index'] for item in matrix_neighbors_gower])
#     matrix_neighbors_gower_values = np.array([item['values'] for item in matrix_neighbors_gower])
#     print(matrix_neighbors_gower_index)

#     # Initialize a list to store the mapped indices
#     mapped_matrix_neighbors_gower_index = []

#     # Loop through each row
#     for row in matrix_neighbors_gower_index:
#         # Map the indices in the current row to their original values
#         mapped_row = np.array([reverse_index_mapping[idx] for idx in row])
#         #print(mapped_row)
#         # Append the mapped row to the list
#         mapped_matrix_neighbors_gower_index.append(mapped_row)

#     # Convert the list of mapped rows to a NumPy array
#     mapped_matrix_neighbors_gower_index = np.array(mapped_matrix_neighbors_gower_index)
#     #print(mapped_matrix_neighbors_gower_index)

#     return mapped_matrix_neighbors_gower_index, matrix_neighbors_gower_values


In [23]:
## Save the 'Group' column from X_train
subgroup_column_train = X_train['Group']
subgroup_column_test = X_test['Group']

# Drop the 'Group' column from X_train
X_train = X_train.drop(columns=['Group'])
X_test = X_test.drop(columns=['Group'])

In [ ]:
# #NOTE: I DO NOT NEED CLOSEST_VALUES_GOWER, I DO NOT NEED TO SAVE TWICE THE MATRIX WITH INDICES (ONE TIME WITH 6 COLUMNS THE SECOND TIME WITH 5 COLUMNS)
# # Now you can compute distances or perform any other operations on X_train without the 'Group' column
# closest_index_gower, closest_values_gower = gower_distance(X_train, cat_features, 5)
# print(closest_index_gower,'\n', closest_values_gower)  #'\n', closest_values_gower)

In [26]:
# Compute 5 nearest neighbors of point_A
nn_model = NearestNeighbors(n_neighbors=6)  # 6 to include itself
nn_model.fit(X_train)
closest_values_gower, closest_index_gower = nn_model.kneighbors(X_train)
# Exclude the first column (index 0) from both arrays
#closest_values_gower = closest_values_gower[:, 1:]
#closest_index_gower = closest_index_gower[:, 1:]



---





---


---

OVERSAMPLE \
NO taxonomy

In [30]:
def custom_smote_notax(X_train, closest_index_gower, cat_features, pu_ix, nu_ix, group_column_train):
    """
    X_train is the training dataset preprocessed, subgroup_column_train is a column containing the subgroup of each
    instance in X_train
    """
    cat_attr_ix = [i for i, value in enumerate(cat_features) if value]
    # Separate minority and majority class points
    #X0 = X_train[group_column_train == 0].values
    #X1 = X_train[group_column_train == 1].values
    X2_df = X_train[group_column_train == pu_ix]
    X2 = X2_df.values
    X3_df = X_train[group_column_train == nu_ix]
    X3 = X3_df.values
    #print(X2_df)
    #PP = len(X0)
    #NP = len(X1)
    PU = len(X2)
    NU = len(X3)

    if (PU / NU) > total_ratio:
        oversampling_target =  (PU / total_ratio) - NU # Oversample NU
        #print(oversampling_target)
        os_df = X3_df
        os_ix = nu_ix
    else:
        oversampling_target = (total_ratio * NU)  - PU # Oversample PU
        #print(oversampling_target)
        os_df = X2_df
        os_ix = pu_ix
    #print(os_ix, 'os_ix')

    #os_df = X2_df
    #os_ix = pu_ix

    # Initialize synthetic samples list
    synthetic_samples = []

    while len(synthetic_samples) < oversampling_target:
        #this is the index of the point
        idx_A = random.choice(os_df.index)
        #print(idx_A)
        point_A = os_df.loc[idx_A]
        #print(point_A, 'punto A')

        nearest_neighbors = np.where(closest_index_gower[:, 0] == idx_A)[0][0]
        nearest_neighbors_indices = closest_index_gower[nearest_neighbors, 1:]
        #print(nearest_neighbors_indices, 'NN ind')

        same_subgroup_indices = [idx for idx in nearest_neighbors_indices if group_column_train.loc[idx] == os_ix]
        #print(same_subgroup_indices)
        if len(same_subgroup_indices) == 0:
            continue

        idx_B = np.random.choice(same_subgroup_indices)
        #print(idx_B, 'indice B')
        point_B = X_train.loc[idx_B]
        #print(point_B, 'point B')

        synthetic_point = np.zeros(len(point_A))
        for i in range(len(point_A)):
            if i in cat_attr_ix:
                neighbor_values = [X_train.loc[idx, X_train.columns[i]] for idx in same_subgroup_indices]
                #print(neighbor_values, 'neig values')
                synthetic_point[i] = max(set(neighbor_values), key=neighbor_values.count)
                #print(synthetic_point[i])
            else:
                epsilon = 1e-10
                alpha = np.random.rand() * (1 - 2 * epsilon) + epsilon
                synthetic_point[i] = point_A[i] + alpha * (point_B[i] - point_A[i])

        synthetic_samples.append(synthetic_point)

    synthetic_samples = np.array(synthetic_samples)

    return synthetic_samples, len(synthetic_samples), os_ix


In [31]:
def oversample_groups(X_train, closest_index_gower, cat_features, custom_smote, group_pairs, group_column_train):
    synthetic_samples = []
    synthetic_samples_group = []
    oversample_method = custom_smote
    subgroup_column_train = group_column_train

    for pu, nu in group_pairs:
        synthetic_points, synthetic_count, os_ix = oversample_method(X_train, closest_index_gower, cat_features, pu, nu, subgroup_column_train)
        # Add a column of 'pu' values to synthetic_points
        pu_column = np.full((len(synthetic_points), 1), os_ix)
        synthetic_samples.append(synthetic_points)
        synthetic_samples_group.append(pu_column)
        print(f"Oversampling for groups {pu} (positive) and {nu} (negative): Added {synthetic_count} synthetic samples in group {os_ix}.")

    # Concatenate all synthetic samples into a single matrix
    synthetic_samples_matrix = np.vstack(synthetic_samples)
    synthetic_samples_group = np.vstack(synthetic_samples_group).flatten()

    return synthetic_samples_matrix, synthetic_samples_group

In [32]:
group_pairs = [(0, 1), (2, 3), (4, 5), (6, 7)] #(0, 1),

#matrix containing all the new synthetic samples, columns containing their subgroup class label
synthetic_samples_matrix_notax, synthetic_samples_group_notax = oversample_groups(X_train, closest_index_gower, cat_features, custom_smote_notax, group_pairs, subgroup_column_train)

Oversampling for groups 0 (positive) and 1 (negative): Added 22 synthetic samples in group 1.
Oversampling for groups 2 (positive) and 3 (negative): Added 14 synthetic samples in group 2.
Oversampling for groups 4 (positive) and 5 (negative): Added 13 synthetic samples in group 4.
Oversampling for groups 6 (positive) and 7 (negative): Added 25 synthetic samples in group 6.


In [33]:
X_train_resampled_notax = pd.concat([X_train, pd.DataFrame(synthetic_samples_matrix_notax, columns=X_train.columns)], ignore_index=True)
#closest_index_gower_resampled, closest_values_gower_resampled = gower_distance(X_train_resampled_notax, cat_features, 5)
#print(closest_index_gower_resampled, 'closest index gower resampled')
subgroup_column_resampled_notax = pd.concat([subgroup_column_train, pd.Series(synthetic_samples_group_notax)], ignore_index=True)
#taxonomy_df_resampled = compute_taxonomy_df(X_train_resampled_notax, subgroup_column_resampled_notax, closest_index_gower_resampled)
#print(taxonomy_df_resampled, 'taxonomy resampled')



---


---

OVERSAMPLE \
taxonomy

In [34]:
def custom_smote_tax(X_train, closest_index_gower, cat_features, pu_ix, nu_ix, group_column_train, s=0.1, b=0.8, r=0.1, o=0):
    """
    X_train is the training dataset preprocessed, subgroup_column_train is a column containing the subgroup of each
    instance in X_train
    """
    cat_attr_ix = [i for i, value in enumerate(cat_features) if value]

    #[0, 0.4, 0.6] [0, 0.5, 0.5] [0.33,0.33,0.33] [0.2, 0.7, 0.1] [0.1, 0.8, 0.1]
    # Separate minority and majority class points
    #X0 = X_train[group_column_train == 0].values
    #X1 = X_train[group_column_train == 1].values
    X2_df = X_train[group_column_train == pu_ix]
    X2 = X2_df.values
    X3_df = X_train[group_column_train == nu_ix]
    X3 = X3_df.values

    #PP = len(X0)
    #NP = len(X1)
    PU = len(X2)
    NU = len(X3)

    if (PU / NU) > total_ratio:
        oversampling_target =  (PU / total_ratio) - NU # Oversample NU
        #print(oversampling_target)
        os_df = X3_df
        os_ix = nu_ix
    else:
        oversampling_target = (total_ratio * NU)  - PU # Oversample PU
        #print(oversampling_target)
        os_df = X2_df
        os_ix = pu_ix
    #print(os_ix, 'os_ix')


    #ratio as many as the most priviledged group
    #oversampling_target = (NU * PP) / NP - PU

    #os_df = X2_df
    #os_ix = pu_ix
    # Calculate weights for taxonomy
    weights = calculate_weights_taxonomy(os_df, closest_index_gower, X_train, group_column_train, s, b, r, o)
    #normalize so that the probabilities sum to one
    weights /= np.sum(weights)

    # Initialize synthetic samples list
    synthetic_samples = []

    while len(synthetic_samples) < oversampling_target:
        #this is the index of the point
        idx_A = np.random.choice(os_df.index, p=weights)
        #print(idx_A)
        point_A = os_df.loc[idx_A]
        #print(point_A, 'punto A')
        nearest_neighbors = np.where(closest_index_gower[:, 0] == idx_A)[0][0]
        nearest_neighbors_indices = closest_index_gower[nearest_neighbors, 1:]
        same_subgroup_indices = [idx for idx in nearest_neighbors_indices if group_column_train.loc[idx] == os_ix]
        #print(same_subgroup_indices)

        if len(same_subgroup_indices) == 0:
            continue

        idx_B = np.random.choice(same_subgroup_indices)
        #print(idx_B, 'indice B')
        point_B = X_train.loc[idx_B]
        #print(point_B, 'point B')

        synthetic_point = np.zeros(len(point_A))
        for i in range(len(point_A)):
            if i in cat_attr_ix:
                neighbor_values = [X_train.loc[idx, X_train.columns[i]] for idx in same_subgroup_indices]
                #print(neighbor_values, 'neig values')
                synthetic_point[i] = max(set(neighbor_values), key=neighbor_values.count)
                #print(synthetic_point[i])
            else:
                epsilon = 1e-10
                alpha = np.random.rand() * (1 - 2 * epsilon) + epsilon
                synthetic_point[i] = point_A[i] + alpha * (point_B[i] - point_A[i])

        synthetic_samples.append(synthetic_point)

    synthetic_samples = np.array(synthetic_samples)

    return synthetic_samples, len(synthetic_samples), os_ix

def calculate_weights_taxonomy(X2_df, closest_index_gower, X_train, group_column_train, s, b, r, o):
    weights = np.zeros(len(X2_df))

    for ix in range(0, len(X2_df)):
        #print(X2_df, 'X2_df')
        idx_complete_df = X2_df.index[ix]
        #print(idx_complete_df, 'indice nel dataset completo')
        nearest_neighbors = np.where(closest_index_gower[:,0] == idx_complete_df)[0][0]
        nearest_neighbors_indices = closest_index_gower[nearest_neighbors, 1:]
        #print(nearest_neighbors_indices, 'NN speriamo')

        same_subgroup_indices = [idx for idx in nearest_neighbors_indices if group_column_train.loc[idx] == group_column_train.loc[idx_complete_df]]
        #print(same_subgroup_indices)

        if len(same_subgroup_indices) == 5 or len(same_subgroup_indices) == 4:
            weights[ix] = s
        elif len(same_subgroup_indices) == 3 or len(same_subgroup_indices) == 2:
            weights[ix] = b
        elif len(same_subgroup_indices) == 1:
            solo_neighbor = same_subgroup_indices[0]
            #print(solo_neighbor, 'solo neigh indx')
            solo_neighbor_row = np.where(closest_index_gower[:, 0] == solo_neighbor)[0][0]
            #print(solo_neighbor_row, 'rowwww')
            neighbors_of_solo_neighbor = closest_index_gower[solo_neighbor_row, 1:]
            #print(neighbors_of_solo_neighbor, 'neigh solo')


            same_class_neighbors = sum(
                1 for neighbor_index in neighbors_of_solo_neighbor if group_column_train.loc[neighbor_index] == group_column_train.loc[idx_complete_df]
            )
            #print(same_class_neighbors, 'same class nei')

            if same_class_neighbors == 0 or same_class_neighbors == 1:
                weights[ix] = r
            else:
                weights[ix] = b
        elif len(same_subgroup_indices) == 0:
            weights[ix] = o
        else:
            weights[ix] = b

    return weights

In [35]:
group_pairs = [(0, 1), (2, 3), (4, 5), (6, 7)] #(0, 1),

#matrix containing all the new synthetic samples, columns containing their subgroup class label
synthetic_samples_matrix_tax, synthetic_samples_group_tax = oversample_groups(X_train, closest_index_gower, cat_features, custom_smote_tax, group_pairs, subgroup_column_train)

Oversampling for groups 0 (positive) and 1 (negative): Added 22 synthetic samples in group 1.
Oversampling for groups 2 (positive) and 3 (negative): Added 14 synthetic samples in group 2.
Oversampling for groups 4 (positive) and 5 (negative): Added 13 synthetic samples in group 4.
Oversampling for groups 6 (positive) and 7 (negative): Added 25 synthetic samples in group 6.


In [36]:
X_train_resampled_tax = pd.concat([X_train, pd.DataFrame(synthetic_samples_matrix_tax, columns=X_train.columns)], ignore_index=True)
#closest_index_gower_resampled, closest_values_gower_resampled = gower_distance(X_train_resampled_tax, cat_features, 5)
#print(closest_index_gower_resampled)
subgroup_column_resampled_tax = pd.concat([subgroup_column_train, pd.Series(synthetic_samples_group_tax)], ignore_index=True)
#taxonomy_df_resampled = compute_taxonomy_df(X_train_resampled_tax, subgroup_column_resampled_tax, closest_index_gower_resampled)
#print(taxonomy_df_resampled, 'taxonomy resampled')



---



---

OVERSAMPLE - USING SMOTENC

In [37]:
def custom_smotenc(X_train, closest_index_gower, cat_features, pu_ix, nu_ix, group_column_train):
    """
    X_train is the training dataset preprocessed, subgroup_column_train is a column containing the subgroup of each
    instance in X_train
    """
    cat_attr_ix = [i for i, value in enumerate(cat_features) if value]
    X2_df = X_train[group_column_train == pu_ix]
    X2 = X2_df.values
    X2_df = X2_df.reset_index(drop=True)  # Reset indices

    X3_df = X_train[group_column_train == nu_ix]
    X3 = X3_df.values
    X3_df = X3_df.reset_index(drop=True)  # Reset indices
    PU = len(X2)
    NU = len(X3)

    if (PU / NU) > total_ratio:
        oversampling_target =  (PU / total_ratio) - NU # Oversample NU
        os_df = X3_df
        os_ix = nu_ix
    else:
        oversampling_target = (total_ratio * NU)  - PU # Oversample PU
        os_df = X2_df
        os_ix = pu_ix

    synthetic_samples = []

    while len(synthetic_samples) < oversampling_target:
        idx_A = random.choice(os_df.index)
        print(idx_A, 'indice A')
        point_A = os_df.loc[idx_A]
        #print(point_A, 'punto A')

        # Compute 5 nearest neighbors of point_A
        nn_model = NearestNeighbors(n_neighbors=6)  # 6 to include itself
        nn_model.fit(os_df)
        dists, nn_indices = nn_model.kneighbors([point_A])
        #print(dists, nn_indices, 'distanze e indici')

        # Exclude the first column (index 0) from both arrays
        dists = dists[:, 1:]
        nn_indices = nn_indices[:, 1:]

        # Select a random point between the 5 nearest neighbors
        idx_B = random.choice(nn_indices[0][1:])
        print(idx_B, 'indice B')
        point_B = os_df.loc[idx_B]


        synthetic_point = np.zeros(len(point_A))
        for i in range(len(point_A)):
            if i in cat_attr_ix:  # Categorical feature
                neighbor_values = [os_df.iloc[idx][i] for idx in nn_indices[0][1:]]
                synthetic_point[i] = max(set(neighbor_values), key=neighbor_values.count)
            else:  # Numerical feature
                alpha = np.random.rand()
                synthetic_point[i] = point_A[i] + alpha * (point_B[i] - point_A[i])

        synthetic_samples.append(synthetic_point)

    synthetic_samples = np.array(synthetic_samples)

    return synthetic_samples, len(synthetic_samples), os_ix


In [38]:
group_pairs = [(0, 1), (2, 3), (4, 5), (6, 7)] #(0, 1),

#matrix containing all the new synthetic samples, columns containing their subgroup class label
synthetic_samples_matrix_smotenc, synthetic_samples_group_smotenc = oversample_groups(X_train, closest_index_gower, cat_features, custom_smotenc, group_pairs, subgroup_column_train)

99 indice A
13 indice B
114 indice A
41 indice B
99 indice A
43 indice B
51 indice A
8 indice B
91 indice A
112 indice B
18 indice A
81 indice B
19 indice A
83 indice B
115 indice A
83 indice B
111 indice A
60 indice B
70 indice A
64 indice B
36 indice A
56 indice B
105 indice A
86 indice B
39 indice A
81 indice B
72 indice A
54 indice B
109 indice A
83 indice B
53 indice A
108 indice B
78 indice A
112 indice B
4 indice A
107 indice B
15 indice A
28 indice B
41 indice A
15 indice B
5 indice A
79 indice B
107 indice A
4 indice B
Oversampling for groups 0 (positive) and 1 (negative): Added 22 synthetic samples in group 1.
13 indice A
25 indice B
5 indice A
10 indice B
6 indice A
0 indice B
7 indice A
20 indice B
14 indice A
20 indice B
2 indice A
21 indice B
19 indice A
15 indice B
8 indice A
2 indice B
4 indice A
20 indice B
12 indice A
19 indice B
26 indice A
1 indice B
24 indice A
16 indice B
21 indice A
11 indice B
13 indice A
9 indice B
Oversampling for groups 2 (positive) and 3 (ne

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature n

In [39]:
X_train_resampled_smotenc = pd.concat([X_train, pd.DataFrame(synthetic_samples_matrix_smotenc, columns=X_train.columns)], ignore_index=True)
#closest_index_gower_resampled, closest_values_gower_resampled = gower_distance(X_train_resampled_tax, cat_features, 5)
#print(closest_index_gower_resampled)
subgroup_column_resampled_smotenc = pd.concat([subgroup_column_train, pd.Series(synthetic_samples_group_smotenc)], ignore_index=True)
#taxonomy_df_resampled = compute_taxonomy_df(X_train_resampled_tax, subgroup_column_resampled_tax, closest_index_gower_resampled)
#print(taxonomy_df_resampled, 'taxonomy resampled')



---



---

TRAIN A CLASSIFIER (LOGREG)

In [40]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import f1_score
from aif360.datasets import BinaryLabelDataset
from aif360.metrics import BinaryLabelDatasetMetric
from aif360.metrics import ClassificationMetric
from aif360.metrics import utils
from sklearn.metrics import balanced_accuracy_score, f1_score, precision_score, recall_score
from aif360.algorithms.preprocessing import *
from aif360.algorithms.preprocessing.optim_preproc_helpers import distortion_functions, opt_tools
from aif360.algorithms.inprocessing import *
from aif360.algorithms.postprocessing import *
import tensorflow
import math

In [41]:
def evaluate(test_data, pred, priv_group, unpriv_group):
    """
    Return the performance and fairness results based on the original data and the predictions.

    test_data : (BinaryLabelDataset) ground truth labels
    pred : (BinaryLabelDataset) predicted labels
    priv_group : (list(dict)) representation of the privileged group
    unpriv_group : (list(dict)) representation of the unprivileged group
    """
    #Evaluation of the model
    cm = ClassificationMetric(test_data, pred, unprivileged_groups=unpriv_group, privileged_groups=priv_group)
    dm = BinaryLabelDatasetMetric(pred, unprivileged_groups=unpriv_group, privileged_groups=priv_group)

    # priv_cond = utils.compute_boolean_conditioning_vector(
    #                         test_data.protected_attributes,
    #                         test_data.protected_attribute_names,
    #                         condition=priv_group)
    # unpriv_cond = utils.compute_boolean_conditioning_vector(
    #                         test_data.protected_attributes,
    #                         test_data.protected_attribute_names,
    #                         condition=unpriv_group)
    #print((priv_cond), (unpriv_cond))
    #print(priv_group)
    # privs_orig = test_data.labels[priv_cond]
    # unprivs_orig = test_data.labels[unpriv_cond]
    # privs_pred = pred.labels[priv_cond]
    # unprivs_pred = pred.labels[unpriv_cond]

    # Concatenate privs_orig and unprivs_orig
    # all_orig_labels = np.concatenate([privs_orig, unprivs_orig])

    # # Concatenate privs_pred and unprivs_pred
    # all_pred_labels = np.concatenate([privs_pred, unprivs_pred])
    # print(len(privs_orig), len(unprivs_orig), len(privs_pred), len(unprivs_pred))

    measure_scores = {
        'b_acc': balanced_accuracy_score(test_data.labels, pred.labels),
        'acc' : cm.accuracy(),
        'precision': precision_score(test_data.labels, pred.labels),
        'recall': recall_score(test_data.labels, pred.labels),
        'f1': f1_score(test_data.labels, pred.labels),
        'SP' : dm.disparate_impact(),
        'AOD' : cm.average_odds_difference(),
        'TPR': (cm.true_positive_rate_difference()),
        'FPR': (cm.false_positive_rate_difference()),
        'C'  : dm.consistency()[0],
        'TNR': (cm.true_negative_rate(privileged=True)-cm.true_negative_rate(privileged=False)),
        'FNR': cm.false_negative_rate_difference(),
        'PPV': (cm.positive_predictive_value(privileged=True)-cm.positive_predictive_value(privileged=False)),
        'FDR': cm.false_discovery_rate_difference(),
        'confmat' : cm.binary_confusion_matrix()
    }

    measure_names = ['b_acc', 'acc', 'precision', 'recall', 'f1', 'SP', 'AOD', 'TPR', 'FPR', 'C', 'TNR', 'FNR', 'PPV', 'FDR', 'confmat']
    results = [measure_scores[elem] for elem in measure_names]

    return results


In [42]:
def evaluate_model_performance(X_train, X_test, privileged_groups, unprivileged_groups, weights=None):
    # Define the protected attributes
    protected_attributes = ['personal_status', 'age']

    # If weights is not provided, create an array of ones with the same length as X_train
    if weights is None:
        weights = np.ones(len(X_train))

    # Define the label and favorable/unfavorable labels
    label_name = 'credit'
    favorable_label = 1
    unfavorable_label = 0

    # Create BinaryLabelDataset for training and testing data
    binary_ds_train = BinaryLabelDataset(df=X_train, label_names=[label_name],
                                         protected_attribute_names=protected_attributes,
                                         favorable_label=favorable_label, unfavorable_label=unfavorable_label)
    binary_ds_test = BinaryLabelDataset(df=X_test, label_names=[label_name],
                                        protected_attribute_names=protected_attributes,
                                        favorable_label=favorable_label, unfavorable_label=unfavorable_label)

    # Calculate metrics for original dataset
    metric_orig_train = BinaryLabelDatasetMetric(binary_ds_train,
                                                 unprivileged_groups=unprivileged_groups,
                                                 privileged_groups=privileged_groups)
    print("Disparate impact (of original labels) = %f" % metric_orig_train.disparate_impact())
    print("Difference in statistical parity (of original labels) = %f"
          % metric_orig_train.statistical_parity_difference())
    print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())

     # Calculate metrics for original dataset
    metric_orig_test = BinaryLabelDatasetMetric(binary_ds_test,
                                                 unprivileged_groups=unprivileged_groups,
                                                 privileged_groups=privileged_groups)
    print("Disparate impact (of original labels) (test) = %f" % metric_orig_test.disparate_impact())
    print("Difference in statistical parity (of original labels) (test) = %f"
          % metric_orig_test.statistical_parity_difference())
    print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())

    # Train a logistic regression model
    logreg = LogisticRegression()
    logreg.fit(X_train.drop(columns= [label_name]), X_train[label_name], sample_weight=weights) #columns= [label_name] + protected_attributes

    # Test the model on the test dataset
    result_LR = logreg.predict(X_test.drop(columns= [label_name])) #columns= [label_name] + protected_attributes

    # Display the confusion matrix
    print(confusion_matrix(result_LR, X_test[label_name]))

    # Create BinaryLabelDataset for predicted test data
    X_test_with_label_predict = pd.concat([X_test.drop(columns=[label_name]), pd.Series(result_LR, name=label_name,
                                                                                       index=X_test.index)], axis=1)
    binary_ds_test_pred = BinaryLabelDataset(df=X_test_with_label_predict, label_names=[label_name],
                                             protected_attribute_names=protected_attributes,
                                             favorable_label=favorable_label, unfavorable_label=unfavorable_label)

    # Evaluate model performance using evaluate method
    results = evaluate(binary_ds_test, binary_ds_test_pred, priv_group=privileged_groups, unpriv_group=unprivileged_groups)

    return results




---



---

Dataset original

In [43]:
# Define privileged and unprivileged groups
privileged_groups = [{'personal_status': 1, 'age': 1}]
unprivileged_groups = [{'personal_status': 0, 'age': 0}]

# Evaluate model performance
results_orig = evaluate_model_performance(X_train, X_test, privileged_groups, unprivileged_groups)

Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.742000
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 44  27]
 [ 46 183]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())




---



---

Dataset resampled no tax

In [44]:
# Evaluate model performance
results_notax = evaluate_model_performance(X_train_resampled_notax, X_test, privileged_groups, unprivileged_groups)

Disparate impact (of original labels) = 1.004339
Difference in statistical parity (of original labels) = 0.003035
Individual fairness metric (consistency) = 0.767959
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 42  26]
 [ 48 184]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())




---



---

Dataset resampled tax

In [45]:
# Evaluate model performance
#[0, 0.4, 0.6] [0, 0.5, 0.5] [0.33,0.33,0.33] [0.2, 0.7, 0.1] [0.1, 0.8, 0.1]
results_tax = evaluate_model_performance(X_train_resampled_tax, X_test, privileged_groups, unprivileged_groups)

Disparate impact (of original labels) = 1.004339
Difference in statistical parity (of original labels) = 0.003035
Individual fairness metric (consistency) = 0.772610
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 44  26]
 [ 46 184]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())




---



---

Dataset resampled SMOTENC


In [46]:
# Evaluate model performance
results_smotenc = evaluate_model_performance(X_train_resampled_smotenc, X_test, privileged_groups, unprivileged_groups)

Disparate impact (of original labels) = 1.004339
Difference in statistical parity (of original labels) = 0.003035
Individual fairness metric (consistency) = 0.759432
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 41  23]
 [ 49 187]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())





---


---


---

OTHER MITIGATION ALGORITHMS - FAIR-SMOTE, REWEIGHING, GERRYFAIR, REMEDY



---


---


---

Fair-SMOTE

In [47]:
!git clone https://github.com/joymallyac/Fair-SMOTE.git

Cloning into 'Fair-SMOTE'...
remote: Enumerating objects: 42, done.
remote: Counting objects: 100% (42/42), done.
remote: Compressing objects: 100% (25/25), done.
remote: Total 42 (delta 14), reused 42 (delta 14), pack-reused 0
Receiving objects: 100% (42/42), 3.35 MiB | 8.28 MiB/s, done.
Resolving deltas: 100% (14/14), done.


In [48]:
import sys
# Define the new list of directories
new_path = ['/content/Fair-SMOTE']  # Adjust the path as needed

# Replace sys.path with the new list
sys.path = new_path
print(sys.path)

from Generate_Samples import generate_samples
from Measure import measure_final_score, calculate_recall, calculate_far, calculate_precision, calculate_accuracy
from SMOTE import smote

['/content/Fair-SMOTE']


/content/Fair-SMOTE/Measure.py:138: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  if (TP + FN) is not 0:
/content/Fair-SMOTE/Measure.py:145: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  if (FP + TN) is not 0:
/content/Fair-SMOTE/Measure.py:152: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  if (TP + FP) is not 0:


In [49]:
def oversample_fair_smote(X_train, group_counts_train, protected_attribute1, protected_attribute2):
    # Extracting group counts
    zero_zero_zero = group_counts_train[7]
    zero_zero_one = group_counts_train[6]
    zero_one_zero = group_counts_train[5]
    zero_one_one = group_counts_train[4]
    one_zero_zero = group_counts_train[3]
    one_zero_one = group_counts_train[2]
    one_one_zero = group_counts_train[1]
    one_one_one = group_counts_train[0]

    # Finding maximum
    maximum = max(zero_zero_zero, zero_zero_one, zero_one_zero, zero_one_one, one_zero_zero, one_zero_one, one_one_zero, one_one_one)
    print(f"Maximum count: {maximum}")

    # Printing which group has maximum count
    if maximum == zero_zero_zero:
        print("zero_zero_zero is maximum")
    elif maximum == zero_zero_one:
        print("zero_zero_one is maximum")
    elif maximum == zero_one_zero:
        print("zero_one_zero is maximum")
    elif maximum == zero_one_one:
        print("zero_one_one is maximum")
    elif maximum == one_zero_zero:
        print("one_zero_zero is maximum")
    elif maximum == one_zero_one:
        print("one_zero_one is maximum")
    elif maximum == one_one_zero:
        print("one_one_zero is maximum")
    elif maximum == one_one_one:
        print("one_one_one is maximum")

    # Calculating number of samples to be increased for each group
    zero_zero_zero_to_be_increased = maximum - zero_zero_zero
    zero_zero_one_to_be_increased = maximum - zero_zero_one
    zero_one_zero_to_be_increased = maximum - zero_one_zero
    zero_one_one_to_be_increased = maximum - zero_one_one
    one_zero_zero_to_be_increased = maximum - one_zero_zero
    one_zero_one_to_be_increased = maximum - one_zero_one
    one_one_zero_to_be_increased = maximum - one_one_zero
    one_one_one_to_be_increased = maximum - one_one_one

    print(f"Counts to be increased for each group:")
    print(f"zero_zero_zero: {zero_zero_zero_to_be_increased}")
    print(f"zero_zero_one: {zero_zero_one_to_be_increased}")
    print(f"zero_one_zero: {zero_one_zero_to_be_increased}")
    print(f"zero_one_one: {zero_one_one_to_be_increased}")
    print(f"one_zero_zero: {one_zero_zero_to_be_increased}")
    print(f"one_zero_one: {one_zero_one_to_be_increased}")
    print(f"one_one_zero: {one_one_zero_to_be_increased}")
    print(f"one_one_one: {one_one_one_to_be_increased}")

    # Filtering dataframes based on class and protected attributes
    df_zero_zero_zero = X_train[(X_train['credit'] == 0) & (X_train[protected_attribute1] == 0) & (X_train[protected_attribute2] == 0)]
    df_zero_zero_one = X_train[(X_train['credit'] == 1) & (X_train[protected_attribute1] == 0) & (X_train[protected_attribute2] == 0)]
    df_zero_one_zero = X_train[(X_train['credit'] == 0) & (X_train[protected_attribute1] == 0) & (X_train[protected_attribute2] == 1)]
    df_zero_one_one = X_train[(X_train['credit'] == 1) & (X_train[protected_attribute1] == 0) & (X_train[protected_attribute2] == 1)]
    df_one_zero_zero = X_train[(X_train['credit'] == 0) & (X_train[protected_attribute1] == 1) & (X_train[protected_attribute2] == 0)]
    df_one_zero_one = X_train[(X_train['credit'] == 1) & (X_train[protected_attribute1] == 1) & (X_train[protected_attribute2] == 0)]
    df_one_one_zero = X_train[(X_train['credit'] == 0) & (X_train[protected_attribute1] == 1) & (X_train[protected_attribute2] == 1)]
    df_one_one_one = X_train[(X_train['credit'] == 1) & (X_train[protected_attribute1] == 1) & (X_train[protected_attribute2] == 1)]

    df_zero_zero_zero['personal_status'] = df_zero_zero_zero['personal_status'].astype(str)
    df_zero_zero_zero['age'] = df_zero_zero_zero['age'].astype(str)

    df_zero_zero_one['personal_status'] = df_zero_zero_one['personal_status'].astype(str)
    df_zero_zero_one['age'] = df_zero_zero_one['age'].astype(str)

    df_zero_one_zero['personal_status'] = df_zero_one_zero['personal_status'].astype(str)
    df_zero_one_zero['age'] = df_zero_one_zero['age'].astype(str)

    df_zero_one_one['personal_status'] = df_zero_one_one['personal_status'].astype(str)
    df_zero_one_one['age'] = df_zero_one_one['age'].astype(str)

    df_one_zero_zero['personal_status'] = df_one_zero_zero['personal_status'].astype(str)
    df_one_zero_zero['age'] = df_one_zero_zero['age'].astype(str)

    df_one_zero_one['personal_status'] = df_one_zero_one['personal_status'].astype(str)
    df_one_zero_one['age'] = df_one_zero_one['age'].astype(str)

    df_one_one_zero['personal_status'] = df_one_one_zero['personal_status'].astype(str)
    df_one_one_zero['age'] = df_one_one_zero['age'].astype(str)

    df_one_one_one['personal_status'] = df_one_one_one['personal_status'].astype(str)
    df_one_one_one['age'] = df_one_one_one['age'].astype(str)

    #print(df_zero_zero_zero.type)
    # Generating samples for each group
    df_zero_zero_zero = generate_samples(zero_zero_zero_to_be_increased, df_zero_zero_zero, 'Germann')
    df_zero_zero_one = generate_samples(zero_zero_one_to_be_increased, df_zero_zero_one, 'Germann')
    df_zero_one_zero = generate_samples(zero_one_zero_to_be_increased, df_zero_one_zero, 'Germann')
    df_zero_one_one = generate_samples(zero_one_one_to_be_increased, df_zero_one_one, 'Germann')
    df_one_zero_zero = generate_samples(one_zero_zero_to_be_increased, df_one_zero_zero, 'Germann')
    df_one_zero_one = generate_samples(one_zero_one_to_be_increased, df_one_zero_one, 'Germann')
    df_one_one_zero = generate_samples(one_one_zero_to_be_increased, df_one_one_zero, 'Germann')
    df_one_one_one = generate_samples(one_one_one_to_be_increased, df_one_one_one, 'Germann')

    # Concatenating dataframes
    X_train_resampled_fair_smote = pd.concat([df_zero_zero_zero, df_zero_zero_one, df_zero_one_zero, df_zero_one_one,
                                              df_one_zero_zero, df_one_zero_one, df_one_one_zero, df_one_one_one])
    X_train_resampled_fair_smote.columns = X_train.columns

    return X_train_resampled_fair_smote



In [50]:
protected_attribute1 = 'personal_status'
protected_attribute2 = 'age'

In [51]:
X_train_resampled_fair_smote = oversample_fair_smote(X_train, group_counts_train, protected_attribute1, protected_attribute2)

Maximum count: 321
one_one_one is maximum
Counts to be increased for each group:
zero_zero_zero: 296
zero_zero_one: 287
zero_one_zero: 270
zero_one_one: 214
one_zero_zero: 303
one_zero_one: 293
one_one_zero: 205
one_one_one: 0


<ipython-input-49-b6963ac077b7>:64: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_zero_zero_zero['personal_status'] = df_zero_zero_zero['personal_status'].astype(str)
<ipython-input-49-b6963ac077b7>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_zero_zero_zero['age'] = df_zero_zero_zero['age'].astype(str)
<ipython-input-49-b6963ac077b7>:67: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the cav

In [52]:
# Evaluate model performance
results_fair_smote = evaluate_model_performance(X_train_resampled_fair_smote, X_test, privileged_groups, unprivileged_groups)

Disparate impact (of original labels) = 1.000000
Difference in statistical parity (of original labels) = 0.000000
Individual fairness metric (consistency) = 0.918925
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 55  41]
 [ 35 169]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())




---



---



---

REWEIGHING - https://github.com/Trusted-AI/AIF360/blob/main/examples/demo_reweighing_preproc.ipynb

In [53]:
!git clone https://github.com/IBM/AIF360.git

Cloning into 'AIF360'...
remote: Enumerating objects: 3853, done.
remote: Counting objects: 100% (3853/3853), done.
remote: Compressing objects: 100% (1434/1434), done.
remote: Total 3853 (delta 2448), reused 3552 (delta 2336), pack-reused 0
Receiving objects: 100% (3853/3853), 7.74 MiB | 9.17 MiB/s, done.
Resolving deltas: 100% (2448/2448), done.


In [54]:
#from aif360.algorithms.preprocessing.reweighing import Reweighing
new_path = ['/content']
sys.path = new_path
from reweighing_cust import Reweighing
# from aif360.algorithms.preprocessing.optim_preproc_helpers.data_preproc_functions\
#         import load_preproc_data_adult, load_preproc_data_german, load_preproc_data_compas

In [55]:
class CustomDataFrame(pd.DataFrame):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, **kwargs)
        self.protected_attribute_names = ['personal_status', 'age']
        self.protected_attributes = np.column_stack([self['personal_status'], self['age']])
        self.labels = self['credit'].values.reshape(-1, 1)
        self.favorable_label = 1
        self.unfavorable_label = 0
        self.instance_weights = np.ones(len(self))
        self.privileged_protected_attributes = [np.array([1.]), np.array([1.])]
        self.unprivileged_protected_attributes = [np.array([0.]), np.array([0.])]
        self.feature_names = self.columns[self.columns != 'credit'].tolist()

X_train = CustomDataFrame(X_train)

<ipython-input-55-d878bbf66640>:4: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  self.protected_attribute_names = ['personal_status', 'age']
<ipython-input-55-d878bbf66640>:5: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  self.protected_attributes = np.column_stack([self['personal_status'], self['age']])
<ipython-input-55-d878bbf66640>:6: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  self.labels = self['credit'].values.reshape(-1, 1)
<ipython-input-55-d878bbf66640>:9: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  self.

In [56]:
RW = Reweighing(unprivileged_groups=unprivileged_groups,
               privileged_groups=privileged_groups)

RW.fit(X_train)
dataset_transf_train = RW.transform(X_train)

In [57]:
results_reweighing = evaluate_model_performance(X_train, X_test, privileged_groups, unprivileged_groups, weights=X_train.instance_weights)

Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.742000
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 49  25]
 [ 41 185]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())




---



---



---

GERRY FAIR

In [58]:
import copy
from aif360.algorithms.inprocessing.gerryfair import heatmap
from aif360.algorithms.inprocessing.gerryfair.clean import array_to_tuple
from aif360.algorithms.inprocessing.gerryfair.learner import Learner
from aif360.algorithms.inprocessing.gerryfair.auditor import *
from aif360.algorithms.inprocessing.gerryfair.classifier_history import ClassifierHistory
from aif360.algorithms import Transformer

In [59]:
classifier = GerryFairClassifier(C=10, printflag=True, heatmapflag=False, max_iters=100, gamma=0.01, fairness_def='FP')
# NOTE : fairness definition = FP, so it decreases the values of FPR. FN works bad, SP doesn't work
# even though FPR is small, SP is not that close to 1
protected_attributes = ['personal_status', 'age']
binary_ds_train = BinaryLabelDataset(df=X_train, label_names=['credit'],
                                    protected_attribute_names=protected_attributes,
                                    favorable_label=1, unfavorable_label=0)
binary_ds_test =  BinaryLabelDataset(df=X_test, label_names=['credit'],
                                    protected_attribute_names=protected_attributes,
                                    favorable_label=1, unfavorable_label=0)

# Fit the classifier on the dataset
classifier.fit(binary_ds_train, early_termination=False)

# Make predictions on the test set
binary_ds_test_pred = classifier.predict(binary_ds_test)

# Evaluate model performance using evaluate method
results_gerryF = evaluate(binary_ds_test, binary_ds_test_pred, priv_group=privileged_groups, unpriv_group=unprivileged_groups)

iteration: 1, error: 0.23, fairness violation: 0.010680272108843543, violated group size: 0.13428571428571429
iteration: 2, error: 0.3407142857142857, fairness violation: 0.006789115646258505, violated group size: 0.13428571428571429
iteration: 3, error: 0.3523809523809524, fairness violation: 0.006684807256235839, violated group size: 0.1657142857142857
iteration: 4, error: 0.3467857142857143, fairness violation: 0.0067653061224489846, violated group size: 0.1657142857142857
iteration: 5, error: 0.3405714285714285, fairness violation: 0.0070176870748299425, violated group size: 0.13428571428571429
iteration: 6, error: 0.33214285714285713, fairness violation: 0.007480725623582766, violated group size: 0.1657142857142857
iteration: 7, error: 0.3251020408163265, fairness violation: 0.007360544217687085, violated group size: 0.1657142857142857
iteration: 8, error: 0.3173214285714286, fairness violation: 0.00725170068027211, violated group size: 0.13428571428571429
iteration: 9, error: 0.3



---



---



---

REMEDY

In [60]:
import sys
sys.path.append('/content')  # Add the directory containing remedy_cust.py to the Python path
from remedy_cust import *

In [61]:
#columns_all = ["List of all of the columns in the dataset except y_label"]
columns_all = X_train.drop(columns=['credit'])

#compas_y = "column name of y_label"
label_y = 'credit'

#columns_compas = ["List of all of the protected attributes in the dataset"]
columns_protected = ['personal_status', 'age']

In [62]:
#names = ["Output of get_temp function, all of the attributes for given group"]
#temp2 = ["Output of get_temp function, sum count by group"]
temp2, names = get_temp(X_train, columns_protected, label_y)
print(temp2, names)
#temp2 counts the number of instances for each combination of sensitive attr and label (like my group count)
#names is the list of sensit attr
unfair_group, unfair_names, skew_candidates, unfair_dict = get_unfair_group(columns_protected, [])
#all empty beside skew candidates that is the list of sensitive attr
print(unfair_group, unfair_names, skew_candidates, unfair_dict)
#all_names is a dict that has 0:[], 1:sens attr1, 2:sens attr2, 3:sens attr1, sens attr2. So for each key (number) it
#associates all possible combinations of sens attr
all_names = candidate_groups(skew_candidates, unfair_dict, columns_protected, unfair_names)
#name values is a dict with sens attrib: possible values
names_values = name_val_dict(X_train, names)

all_names_lst = list(all_names.keys())[1:] # CHANGED HERE
all_names_lst.reverse()
#all_names_lst is a list of the keys of the dict all_names, so numbers [3,2,1]
all_names_lst

['personal_status', 'age', 'credit']
   personal_status  age  credit  cnt
0                0    0       0   25
1                0    0       1   34
2                0    1       0   51
3                0    1       1  107
4                1    0       0   18
5                1    0       1   28
6                1    1       0  116
7                1    1       1  321 ['personal_status', 'age']
[] [] ['personal_status', 'age'] {}


/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0


[3, 2, 1]

In [63]:
#get all of the candidate groups possible with the combos and names
filter_count = 30
#copy of the dataset
new_train_data = copy.deepcopy(X_train)
print(new_train_data.shape[0])

#iterate over all the names to get the temp2 df for each name
for a in all_names_lst:
  print("?????/////")
  print(a)
  #temp2 counts the number of instances for each combination of sensitive attr and label (like my group count)
  #names is the list of sensit attr
  temp2, names = get_temp(new_train_data, all_names[a], label_y)
  print(temp2, '\n', names, 'temp2,names \n')
  #temp is a df with the entire columns, where the columns are in the first iteration all sens attr and the label
  # in the second iteration are one sens attrib and the label
  # temp_g counts the instances considering only the sens attrib (first iteration both sens attr, then only one at the time)
  temp, temp_g = get_temp_g(new_train_data, names, label_y)
  print(temp,'\n', temp_g, 'temp,temp_g \n')
  temp_g = temp_g[temp_g['cnt'] > filter_count]
  #lst_of_counts is a list of df, the first df have first sens attr and the credit + count, the second is second sens attr
  #and the credit + count
  lst_of_counts = compute_lst_of_counts(temp, names, label_y)
  print(lst_of_counts, 'listof counts \n')

  need_pos, need_neg = compute_problematic_opt(temp2, temp_g, names, label_y, lst_of_counts)
  print("The sets of need pos and neg are")
  print(need_pos)
  print(need_neg)
  new_train_data['skewed'] = 0
  new_train_data["diff"] = 0
  print("started duplication")
  new_train_data = naive_duplicate(new_train_data, temp2, names, need_pos, need_neg, label_y)
  print(new_train_data.shape[0])
  print("label y ", new_train_data[label_y].value_counts())
#new_train_x = pd.DataFrame(new_train_data, columns = columns_all)
new_train_label = pd.DataFrame(new_train_data, columns = [label_y])
new_train_label = new_train_label[label_y]
new_train_label = new_train_label.astype('int')

700
?????/////
3
['personal_status', 'age', 'credit']
   personal_status  age  credit  cnt
0                0    0       0   25
1                0    0       1   34
2                0    1       0   51
3                0    1       1  107
4                1    0       0   18
5                1    0       1   28
6                1    1       0  116
7                1    1       1  321 
 ['personal_status', 'age'] temp2,names 

     personal_status  age  credit  cnt
0                  1    1       1    0
1                  1    1       1    0
2                  1    1       1    0
3                  1    1       0    0
4                  1    1       1    0
..               ...  ...     ...  ...
695                1    1       1    0
696                1    1       0    0
697                0    1       1    0
698                1    1       1    0
699                1    1       0    0

[700 rows x 4 columns] 
    personal_status  age  cnt
0                0    0   59
1                0

/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0


1.9565217391304348 321 116 48.0666666666667
Adding 48 negative records
names  ['personal_status', 'age'] [1, 1]
801
label y  credit
1    543
0    258
Name: count, dtype: int64
?????/////
2
['age', 'credit']
   age  credit  cnt
0    0       0   43
1    0       1   94
2    1       0  215
3    1       1  449 
 ['age'] temp2,names 

     age  credit  cnt
0      1       1    0
1      1       1    0
2      1       1    0
3      1       0    0
4      1       1    0
..   ...     ...  ...
796    1       0    0
797    1       0    0
798    1       0    0
799    1       0    0
800    1       0    0

[801 rows x 3 columns] 
    age  cnt
0    0  137
1    1  664 temp,temp_g 

[credit
0    258
1    543
Name: cnt, dtype: int64] listof counts 

The sets of need pos and neg are
[]
[]
started duplication
801
label y  credit
1    543
0    258
Name: count, dtype: int64
?????/////
1
['personal_status', 'credit']
   personal_status  credit  cnt
0                0       0   76
1                0       1  177


/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 

In [64]:
X_train_resampled_remedy = new_train_data.drop(columns= ['skewed', 'diff'])

In [65]:
# Evaluate model performance
results_remedy = evaluate_model_performance(X_train_resampled_remedy, X_test, privileged_groups, unprivileged_groups)

Disparate impact (of original labels) = 1.000463
Difference in statistical parity (of original labels) = 0.000306
Individual fairness metric (consistency) = 0.757553
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.760667
[[ 48  28]
 [ 42 182]]


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())




---





---



---

COMPARE

In [66]:
# Define the arrays
arrays = [results_orig, results_notax, results_tax, results_smotenc, results_fair_smote, results_reweighing, results_gerryF, results_remedy]

# Define the headers
headers = ['b_acc', 'acc', 'prec', 'recall', 'f1', 'SP', 'AOD', 'TPR', 'FPR', 'C', 'TNR', 'FNR', 'PPV', 'FDR']

# Transpose the arrays
arrays_transposed = np.transpose(arrays)

print('\t \t none ,wo taxo, w taxo, smonc, fairsm, reweigh, gerryF; remed')
# Print the values with corresponding headers
for header, row in zip(headers, arrays_transposed):
    row_values = ['{:.4f}'.format(value) for value in row]
    print(header +'\t'+ '\t' + '\t'.join(row_values))

print(results_orig[-1])
print(results_notax[-1])
print(results_tax[-1])
print(results_reweighing[-1])
print(results_fair_smote[-1])

	 	 none ,wo taxo, w taxo, smonc, fairsm, reweigh, gerryF; remed
b_acc		0.6802	0.6714	0.6825	0.6730	0.7079	0.7127	0.6913	0.7000
acc		0.7567	0.7533	0.7600	0.7600	0.7467	0.7800	0.7633	0.7667
prec		0.7991	0.7931	0.8000	0.7924	0.8284	0.8186	0.8062	0.8125
recall		0.8714	0.8762	0.8762	0.8905	0.8048	0.8810	0.8714	0.8667
f1		0.8337	0.8326	0.8364	0.8386	0.8164	0.8486	0.8375	0.8387
SP		0.5748	0.9024	0.8021	1.0458	1.1340	0.7019	0.5785	1.0133
AOD		-0.3248	-0.0207	-0.1116	0.0925	0.1721	-0.1962	-0.3148	0.0859
TPR		-0.1915	-0.0269	-0.0269	0.1087	0.1387	-0.0342	-0.1915	0.0663
FPR		-0.4582	-0.0145	-0.1964	0.0764	0.2055	-0.3582	-0.4382	0.1055
C		0.8633	0.8733	0.8740	0.8860	0.8307	0.8773	0.8580	0.8693
TNR		-0.4582	-0.0145	-0.1964	0.0764	0.2055	-0.3582	-0.4382	0.1055
FNR		0.1915	0.0269	0.0269	-0.1087	-0.1387	0.0342	0.1915	-0.0663
PPV		-0.0372	0.1467	0.0633	0.1479	0.1809	-0.0371	-0.0321	0.1598
FDR		-0.0372	0.1467	0.0633	0.1479	0.1809	-0.0371	-0.0321	0.1598
{'TP': 183.0, 'FP': 46.0, 'TN': 44.0, 'FN': 27.0}


In [69]:
class ModelEvaluator:
    def __init__(self, df, protected_attributes, label_name, privileged, unprivileged, fav, unfav, num_iterations=10, oversampling=None):
        self.df = df
        self.protected_attributes = protected_attributes
        self.label_name = label_name
        self.privileged = privileged
        self.unprivileged = unprivileged
        self.fav = fav
        self.unfav = unfav
        self.num_iterations = num_iterations
        self.oversampling = oversampling

    def evaluate_model_performance_mean(self):
        results_list = []

        for _ in range(self.num_iterations):
            # Prepare data
            data_prep = DataPreparation(self.df, self.protected_attributes, self.label_name,
                                        self.privileged, self.unprivileged, self.fav, self.unfav)
            data_prep.prepare()
            data_prep.df = data_prep.df.reset_index(drop=True)
            X_train, X_test = data_prep.X_train, data_prep.X_test
            X_train = X_train.reset_index(drop=True)
            X_test = X_test.reset_index(drop=True)

            cat_features = data_prep.cat_features
            numerical_features = data_prep.numerical_features

            # Count instances from each group in X_train
            group_counts_train = X_train['Group'].value_counts().sort_index()

            # Save the 'Group' column from X_train
            subgroup_column_train = X_train['Group']
            subgroup_column_test = X_test['Group']

            # Drop the 'Group' column from X_train
            X_train = X_train.drop(columns=['Group'])
            X_test = X_test.drop(columns=['Group'])

            total_ratio = (X_train['credit'] == 1).sum() / (X_train['credit'] == 0).sum()

            # Define privileged and unprivileged groups
            # privileged_groups = [{attr: self.favorable_label[i] for i, attr in enumerate(self.protected_attributes)}]
            # unprivileged_groups = [{attr: self.unfavorable_label[i] for i, attr in enumerate(self.protected_attributes)}]
            privileged_groups = [{'personal_status': 1, 'age': 1}]
            unprivileged_groups = [{'personal_status': 0, 'age': 0}]

            if self.oversampling is None:
                results = evaluate_model_performance(X_train, X_test, privileged_groups, unprivileged_groups)
                results_list.append(results[:14])

            elif self.oversampling == 'custom_smote_notax':
                # Compute distances
                #closest_index_gower, closest_values_gower = gower_distance(X_train, cat_features, 5)

                # Compute 5 nearest neighbors of point_A
                nn_model = NearestNeighbors(n_neighbors=6)  # 6 to include itself
                nn_model.fit(X_train)
                closest_values_gower, closest_index_gower = nn_model.kneighbors(X_train)

                # Oversample
                group_pairs = [(0, 1), (2, 3), (4, 5), (6, 7)]
                synthetic_samples_matrix_notax, synthetic_samples_group_notax = oversample_groups(X_train, closest_index_gower,
                                                                                                  cat_features, custom_smote_notax,
                                                                                                  group_pairs, subgroup_column_train)
                # Create resampled matrix
                X_train_resampled_notax = pd.concat([X_train, pd.DataFrame(synthetic_samples_matrix_notax, columns=X_train.columns)],
                                                    ignore_index=True)
                subgroup_column_resampled_notax = pd.concat([subgroup_column_train, pd.Series(synthetic_samples_group_notax)],
                                                            ignore_index=True)
                # Evaluate model performance
                results = evaluate_model_performance(X_train_resampled_notax, X_test, privileged_groups, unprivileged_groups)
                results_list.append(results[:14])

            elif self.oversampling == 'custom_smote_tax':
                # Compute distances
                #closest_index_gower, closest_values_gower = gower_distance(X_train, cat_features, 5)

                # Compute 5 nearest neighbors of point_A
                nn_model = NearestNeighbors(n_neighbors=6)  # 6 to include itself
                nn_model.fit(X_train)
                closest_values_gower, closest_index_gower = nn_model.kneighbors(X_train)

                # Oversample
                group_pairs = [(0, 1), (2, 3), (4, 5), (6, 7)]
                synthetic_samples_matrix_tax, synthetic_samples_group_tax = oversample_groups(X_train, closest_index_gower,
                                                                                              cat_features, custom_smote_tax,
                                                                                                  group_pairs, subgroup_column_train)
                # Create resampled matrix
                X_train_resampled_tax = pd.concat([X_train, pd.DataFrame(synthetic_samples_matrix_tax, columns=X_train.columns)],
                                                    ignore_index=True)
                subgroup_column_resampled_tax = pd.concat([subgroup_column_train, pd.Series(synthetic_samples_group_tax)],
                                                            ignore_index=True)
                # Evaluate model performance
                results = evaluate_model_performance(X_train_resampled_tax, X_test, privileged_groups, unprivileged_groups)
                results_list.append(results[:14])

            elif self.oversampling == 'custom_smotenc':
                closest_index_gower = [1,2]
                # Oversample
                group_pairs = [(0, 1), (2, 3), (4, 5), (6, 7)]
                synthetic_samples_matrix_smotenc, synthetic_samples_group_smotenc = oversample_groups(X_train, closest_index_gower,
                                                                                              cat_features, custom_smotenc,
                                                                                                  group_pairs, subgroup_column_train)
                # Create resampled matrix
                X_train_resampled_smotenc = pd.concat([X_train, pd.DataFrame(synthetic_samples_matrix_smotenc, columns=X_train.columns)],
                                                    ignore_index=True)
                subgroup_column_resampled_smotenc = pd.concat([subgroup_column_train, pd.Series(synthetic_samples_group_smotenc)],
                                                            ignore_index=True)
                # Evaluate model performance
                results = evaluate_model_performance(X_train_resampled_smotenc, X_test, privileged_groups, unprivileged_groups)
                results_list.append(results[:14])

            elif self.oversampling == 'Fair-SMOTE':
                X_train_resampled_fair_smote = oversample_fair_smote(X_train, group_counts_train,
                                                                     protected_attribute1 = 'personal_status',
                                                                     protected_attribute2= 'age')
                # Evaluate model performance
                results = evaluate_model_performance(X_train_resampled_fair_smote, X_test, privileged_groups, unprivileged_groups)
                results_list.append(results[:14])

            elif self.oversampling == 'Reweighing':
                X_train = CustomDataFrame(X_train)
                RW = Reweighing(unprivileged_groups=unprivileged_groups,
                                privileged_groups=privileged_groups)
                RW.fit(X_train)
                dataset_transf_train = RW.transform(X_train)

                # Evaluate model performance
                results = evaluate_model_performance(X_train, X_test, privileged_groups, unprivileged_groups, weights=X_train.instance_weights)
                results_list.append(results[:14])

            elif self.oversampling == 'GerryFair':
                classifier = GerryFairClassifier(C=10, printflag=True, heatmapflag=False, max_iters=100, gamma=0.01, fairness_def='FP')
                # NOTE : fairness definition = FP, so it decreases the values of FPR. FN works bad, SP doesn't work
                # even though FPR is small, SP is not that close to 1
                # protected_attributes = ['personal_status', 'age']
                binary_ds_train = BinaryLabelDataset(df=X_train, label_names=['credit'],
                                                    protected_attribute_names=protected_attributes,
                                                    favorable_label=1, unfavorable_label=0)
                binary_ds_test =  BinaryLabelDataset(df=X_test, label_names=['credit'],
                                                    protected_attribute_names=protected_attributes,
                                                    favorable_label=1, unfavorable_label=0)
                # Fit the classifier on the dataset
                classifier.fit(binary_ds_train, early_termination=True)
                binary_ds_test_pred = classifier.predict(binary_ds_test)

                # Evaluate model performance using evaluate method
                results = evaluate(binary_ds_test, binary_ds_test_pred, priv_group=privileged_groups, unpriv_group=unprivileged_groups)
                results_list.append(results[:14])

            elif self.oversampling == 'Remedy':
                columns_all = X_train.drop(columns=['credit']) #["List of all of the columns in the dataset except y_label"]
                label_y = 'credit' #"column name of y_label"
                columns_protected = ['personal_status', 'age'] #["List of all of the protected attributes in the dataset"]
                temp2, names = get_temp(X_train, columns_protected, label_y)
                unfair_group, unfair_names, skew_candidates, unfair_dict = get_unfair_group(columns_protected, [])
                print(unfair_group, unfair_names, skew_candidates, unfair_dict)
                all_names = candidate_groups(skew_candidates, unfair_dict, columns_protected, unfair_names)
                names_values = name_val_dict(X_train, names)

                all_names_lst = list(all_names.keys())[1:] # CHANGED HERE
                all_names_lst.reverse()
                #get all of the candidate groups possible with the combos and names
                filter_count = 30
                new_train_data = copy.deepcopy(X_train)
                #iterate over all the names to get the temp2 df for each name
                for a in all_names_lst:
                  temp2, names = get_temp(new_train_data, all_names[a], label_y)
                  temp, temp_g = get_temp_g(new_train_data, names, label_y)
                  temp_g = temp_g[temp_g['cnt'] > filter_count]
                  lst_of_counts = compute_lst_of_counts(temp, names, label_y)
                  need_pos, need_neg = compute_problematic_opt(temp2, temp_g, names, label_y, lst_of_counts)
                  new_train_data['skewed'] = 0
                  new_train_data["diff"] = 0
                  new_train_data = naive_duplicate(new_train_data, temp2, names, need_pos, need_neg, label_y)
                #new_train_x = pd.DataFrame(new_train_data, columns = columns_all)
                new_train_label = pd.DataFrame(new_train_data, columns = [label_y])
                new_train_label = new_train_label[label_y]
                new_train_label = new_train_label.astype('int')

                X_train_resampled_remedy = new_train_data.drop(columns= ['skewed', 'diff'])

                results = evaluate_model_performance(X_train_resampled_remedy, X_test, privileged_groups, unprivileged_groups)
                results_list.append(results[:14])

        # Compute the mean of the evaluation results across iterations
        mean_results = np.mean(results_list, axis=0)

        return mean_results

In [70]:
model_evaluator_orig = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10)
results_orig_mean = model_evaluator_orig.evaluate_model_performance_mean()

model_evaluator_notax = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'custom_smote_notax')
results_notax_mean = model_evaluator_notax.evaluate_model_performance_mean()

model_evaluator_tax = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'custom_smote_tax')
results_tax_mean = model_evaluator_tax.evaluate_model_performance_mean()

model_evaluator_smotenc = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'custom_smotenc')
results_smotenc_mean = model_evaluator_smotenc.evaluate_model_performance_mean()

model_evaluator_fair_smote = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'Fair-SMOTE')
results_fair_smote_mean = model_evaluator_fair_smote.evaluate_model_performance_mean()

model_evaluator_reweighing = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'Reweighing')
results_reweighing_mean = model_evaluator_reweighing.evaluate_model_performance_mean()

model_evaluator_gerryfair = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'GerryFair')
results_gerryfair_mean = model_evaluator_gerryfair.evaluate_model_performance_mean()

model_evaluator_remedy = ModelEvaluator(df, ['personal_status', 'age'], 'credit', [1, 1], [0, 0], 1,2, num_iterations=10, oversampling = 'Remedy')
results_remedy_mean = model_evaluator_remedy.evaluate_model_performance_mean()

No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.746000
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.728000
[[ 41  20]
 [ 49 190]]
No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.746286
Disparate impact (of original labels) (test) 

<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())
<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (cons

Individual fairness metric (consistency) (test) = 0.741333
[[ 45  29]
 [ 45 181]]
No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.758000
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.732667
[[ 46  32]
 [ 44 178]]
No missing values detected.
The 'credit' column has only two unique values.


<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) = %f" % metric_orig_train.consistency())
<ipython-input-42-3ebb2983b80c>:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (consistency) (test) = %f" % metric_orig_test.consistency())
<ipython-input-42-3ebb2983b80c>:29: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  print("Individual fairness metric (cons

[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.744571
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.759333
[[ 48  31]
 [ 42 179]]
No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
Disparate impact (of original labels) = 0.784519
Difference in statistical parity (of original labels) = -0.158283
Individual fairness metric (consistency) = 0.747143


...

2.517730496453901 28 18 17.3191489361702
2.517730496453901 28 18 17.3191489361702
Adding 17 positive records
names  ['personal_status', 'age'] [1, 0]
1.9565217391304348 321 116 48.0666666666667
Adding 48 negative records
names  ['personal_status', 'age'] [1, 1]
['age', 'credit']
['personal_status', 'credit']
Disparate impact (of original labels) = 1.000463
Difference in statistical parity (of original labels) = 0.000306
Individual fairness metric (consistency) = 0.765293
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.758667
[[ 40  38]
 [ 50 172]]
No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
['personal_status', 'age', 'credit']
[] [] ['personal_status', 'age'] {}
['personal_status', 'age', 'credit'

/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 

[[ 38  27]
 [ 52 183]]
No missing values detected.
The 'credit' column has only two unique values.
[(0, (1, 1, 1)), (1, (1, 1, 0)), (2, (1, 0, 1)), (3, (1, 0, 0)), (4, (0, 1, 1)), (5, (0, 1, 0)), (6, (0, 0, 1)), (7, (0, 0, 0))]
['personal_status', 'age', 'credit']
[] [] ['personal_status', 'age'] {}
['personal_status', 'age', 'credit']
1.9565217391304348 34 25 14.9130434782609
1.9565217391304348 34 25 14.9130434782609
Adding 15 positive records
names  ['personal_status', 'age'] [0, 0]
2.517730496453901 107 51 21.4042553191489
2.517730496453901 107 51 21.4042553191489
Adding 21 positive records
names  ['personal_status', 'age'] [0, 1]


/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 0
/content/remedy_cust.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['cnt'] = 

2.517730496453901 28 18 17.3191489361702
2.517730496453901 28 18 17.3191489361702
Adding 17 positive records
names  ['personal_status', 'age'] [1, 0]
1.9565217391304348 321 116 48.0666666666667
Adding 48 negative records
names  ['personal_status', 'age'] [1, 1]
['age', 'credit']
['personal_status', 'credit']
Disparate impact (of original labels) = 1.000463
Difference in statistical parity (of original labels) = 0.000306
Individual fairness metric (consistency) = 0.777029
Disparate impact (of original labels) (test) = 0.762899
Difference in statistical parity (of original labels) (test) = -0.174043
Individual fairness metric (consistency) (test) = 0.729333
[[ 40  32]
 [ 50 178]]


In [71]:
# Define the arrays
arrays = [results_orig_mean, results_notax_mean, results_tax_mean, results_smotenc_mean, results_fair_smote_mean, results_reweighing_mean, results_gerryfair_mean, results_remedy_mean]

# Define the headers
headers = ['b_acc', 'acc', 'prec', 'recall', 'f1', 'SP', 'AOD', 'TPR', 'FPR', 'C', 'TNR', 'FNR', 'PPV', 'FDR']

# Transpose the arrays
arrays_transposed = np.transpose(arrays)

print('\t \t none; wo taxo; w taxo; smonc; fairsm; reweigh; gerryF; remed')
# Print the values with corresponding headers
for header, row in zip(headers, arrays_transposed):
    row_values = ['{:.4f}'.format(value) for value in row]
    print(header +'\t'+ '\t' + '\t'.join(row_values))

	 	 none; wo taxo; w taxo; smonc; fairsm; reweigh; gerryF; remed
b_acc		0.6926	0.6748	0.6636	0.6650	0.6531	0.6776	0.6937	0.6548
acc		0.7697	0.7590	0.7543	0.7603	0.7223	0.7593	0.7293	0.7417
prec		0.8053	0.7945	0.7873	0.7863	0.7877	0.7963	0.8265	0.7835
recall		0.8852	0.8852	0.8905	0.9033	0.8262	0.8819	0.7829	0.8719
f1		0.8431	0.8372	0.8354	0.8406	0.8064	0.8369	0.7988	0.8252
SP		0.7146	0.9234	0.9183	0.9621	1.1849	0.8534	0.6086	1.0086
AOD		-0.1883	0.0130	-0.0122	0.0324	0.1959	-0.0617	-0.2296	0.0600
TPR		-0.0723	-0.0478	-0.0171	-0.0187	0.1357	-0.0442	-0.1761	0.0597
FPR		-0.3044	0.0738	-0.0073	0.0836	0.2562	-0.0793	-0.2831	0.0602
C		0.8684	0.8667	0.8729	0.8764	0.8403	0.8691	0.8384	0.8566
TNR		-0.3044	0.0738	-0.0073	0.0836	0.2562	-0.0793	-0.2831	0.0602
FNR		0.0723	0.0478	0.0171	0.0187	-0.1357	0.0442	0.1761	-0.0597
PPV		0.0161	0.1798	0.1455	0.1802	0.2036	0.1198	0.0122	0.1544
FDR		0.0161	0.1798	0.1455	0.1802	0.2036	0.1198	0.0122	0.1544


In [72]:
counts_remedy = X_train_resampled_remedy.groupby(['personal_status', 'age', 'credit']).size()

# Iterate over the groups and print the results
for (personal_status, age, credit), count in counts_remedy.items():
    print(f"Personal Status: {personal_status}, Age: {age}, Credit: {credit}, Count: {count}")

Personal Status: 0, Age: 0, Credit: 0, Count: 25
Personal Status: 0, Age: 0, Credit: 1, Count: 49
Personal Status: 0, Age: 1, Credit: 0, Count: 51
Personal Status: 0, Age: 1, Credit: 1, Count: 128
Personal Status: 1, Age: 0, Credit: 0, Count: 18
Personal Status: 1, Age: 0, Credit: 1, Count: 45
Personal Status: 1, Age: 1, Credit: 0, Count: 164
Personal Status: 1, Age: 1, Credit: 1, Count: 321
